In [1]:
import fn_file as fn

import itertools
from gensim.models import Word2Vec
import pandas as pd
import copy
import re

from khaiii import KhaiiiApi
api = KhaiiiApi()
from multiprocessing import Pool
import time

In [2]:
import imp
imp.reload(fn)

<module 'fn_file' from '/home/kys/fn_file.py'>

In [3]:
def clean_str(text):
    pattern = '([ㄱ-ㅎㅏ-ㅣ]+)'  # 한글 자음, 모음 제거
    text = re.sub(pattern=pattern, repl='', string=text)
    pattern = '<[^>]*>'         # HTML 태그 제거
    text = re.sub(pattern=pattern, repl='', string=text)
    pattern = '[^\w\s]'         # 특수기호제거
    text = re.sub(pattern=pattern, repl='', string=text)
    pattern = '[\{\}\[\]\/?.,;:|\)*~`!^\-_+<>@\#$%&\\\=\(\'\"]' # 특수기호 제거
    text = re.sub(pattern=pattern, repl='', string=text)
    pattern = "\u3000\u3000"     # 유니코드 삭제
    text = re.sub(pattern=pattern, repl='',string=text)
    pattern = re.compile('[\U00010000-\U0010ffff]', flags=re.UNICODE) #마지막점검 제거
    text = re.sub(pattern=pattern, repl='',string=text)
    return text

## 0. 데이터와 w2v 모델 불러오기

In [4]:
morphs =[[]]
with open('for_word2vec.txt') as f:
    for i in range(0,115071):
        for line in f:
            morphs[i].append(line.split(','))
morphs=morphs[0]

for i in range(0,len(morphs)):
    morphs[i][-1] = morphs[i][-1].rstrip('\n')

In [5]:
# w2v모델 불러오기
model_tag = Word2Vec.load('play_w2v.model')

In [6]:
train_data = pd.read_json('train.json', encoding='UTF-8', typ = 'frame')
valid_data = pd.read_json('val.json', encoding='UTF-8', typ = 'frame')
song_meta = pd.read_json('song_meta.json', encoding='UTF-8', typ = 'frame')
genre_gn_all = pd.read_json('genre_gn_all.json',encoding='UTF-8', typ = 'series')
genre_gn_all = pd.DataFrame(genre_gn_all, columns = ['gnr_name']).reset_index().rename(columns = {'index' : 'gnr_code'})

for_genre = copy.deepcopy(song_meta[['song_gn_dtl_gnr_basket','id']])

In [7]:
uniq_tag = list(set(itertools.chain(*train_data.tags)))

for i in range(0,len(uniq_tag)):
    uniq_tag[i] = uniq_tag[i].lower()

In [8]:
# validation data 복사본 만들어두기
prac = copy.deepcopy(valid_data[['tags','plylst_title','songs','updt_date','like_cnt']])

In [9]:
for i in range(0,len(prac)):
    mylist = [[prac['plylst_title'][i]]]
    clean = clean_str(' '.join(sum(mylist,[])))
    if len(clean)==0:
        clean=' '
    prac['plylst_title'][i] = clean
    
for i in range(len(prac['plylst_title'])):
    prac['plylst_title'][i]=prac['plylst_title'][i].strip()

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  if __name__ == '__main__':


## 1. 형태소 추출

In [10]:
def do_work(i):
    tmp_list = []
    noun_list = []
    if len(prac['plylst_title'][i]) == prac['plylst_title'][i].count(' '):
        # 빈칸으로만 되어있는 행
        pass
    elif prac['plylst_title'][i].find(" ")==-1:
        # 띄어쓰기 없는 행
        tmp_list.append(prac['plylst_title'][i])
        noun_list.append(prac['plylst_title'][i])
    else:
        for word in api.analyze(prac['plylst_title'][i]):
            for morph in word.morphs:
                # 실질형태소 가져오기
                if morph.tag in ['NNG', 'NNP', 'NP', 'VV', 'VA', 'XR', 'IC', 'MM', 'MAG', 'MAJ','SN','SL']:
                    tmp_list.append(morph.lex)
                if morph.tag in ['NNG','NNP','NP','SL']:
                    noun_list.append(morph.lex)
    if i%100==0:
        print(i)
    if i%1000==0:
        time.sleep(5)
        
    return [tmp_list, noun_list]



if __name__ == '__main__':
    start_time = time.time()
    with Pool(processes=7) as p:
        result= p.map(do_work, range(0,len(prac['plylst_title'])))
    print("--- %s seconds ---" % (time.time()-start_time))

0
3300
2500
1700
5000900

4200
18003400

2600
10004300

44003500

2700
4500
1900
3600
2800
46002000

3700
2900
4700
3800
3000
4800
3900
4900
4000
5800
5900
6000
100
5100200

5200300

1100
5300400

1200
5400
1300500

2100
1400
5500
600
2200
1500
5600
2300
3100700

1600
8005700

7400

24004100

66003200
83009100

670075009900


6100
107009200

8400
6800
620010000

10800
7600
6300
9300
6900
10900
940077008500

7000

6400
11000
7800
6500
9500
8600
7900
8700
9600
8800
80009700

11600
8900
9800
117009000

12400
11800
12500
11900
12600
12000
12700
12800
12900
13000
10100
10200
103007100

11100
104007200

1120010500

7300
11300
810010600

11400
820013200

14000
14800
13300
11500
14900
15700
13400
16500
15000
15800
13500
12100
13600
1590016600

12200
16700
13700
16000
12300
13800
17300
16800
13900
13100
17400
18100
16900
18200
17500
17000
19000
17600
18300
17700
18400
17800
18500
17900
18600
18700
18000
18800
18900
19800
19900
20000
14100
14200
14300
15100
14400
15200
14500
15300
14600
15400
16

### 1-1. 형태소 추출 된것 전처리

In [11]:
### 영어 소문자로
for i in range(len(result)):
    for j in range(len(result[i])):
        for z in range(len(result[i][j])):
            result[i][j][z] = result[i][j][z].lower()

### 영어 한글자 지우기
import re
p = re.compile('[a-z]')

for i in range(len(result)):
    for j in range(len(result[i])):
        for z in range(len(result[i][j])):
            if len(result[i][j][z]) == 1:
                if p.match(result[i][j][z]) != None:
                    result[i][j][z] = ''

for i in range(len(result)):
    for j in range(len(result[i])):
        while '' in result[i][j]:
            result[i][j].remove('')
            
### 중복되는 단어 제거
for i in range(len(result)):
    for j in range(len(result[i])):
        result[i][j] = list(set(result[i][j]))

### 숫자 4자리 제외 제거
for i in range(len(result)):
    for j in range(len(result[i])):
        for z in range(len(result[i][j])):
            if result[i][j][z].isdigit() == True:
                if len(result[i][j][z]) != 4:
                    result[i][j][z] = ''
                    
for i in range(len(result)):
    for j in range(len(result[i])):
        while '' in result[i][j]:
            result[i][j].remove('')

In [12]:
full_list = []
noun_list = []

for lst in result:
    full_list.append(lst[0])
    noun_list.append(lst[1])

### 1-2. validation 데이터 완성(prac)
 - 미연의 일을 방지하기 위해서 valid의 복사본인 prac 만듦.

In [13]:
prac['plylst_title']=copy.deepcopy(full_list)
prac['nouns']=copy.deepcopy(noun_list)
pred_tag=[]
pred_song=[]
for i in range(len(prac)):
    pred_tag.append([])
for i in range(len(prac)):
    pred_song.append([])
prac['pred_song']=pred_song
prac['pred_tag']=pred_tag
prac['index'] = range(len(prac))
prac = prac[['index','tags','plylst_title','nouns','songs','updt_date','pred_tag','pred_song','like_cnt']]

### 들어있는 tag 영어 소문자로
for i in range(0,len(prac['tags'])):
    for j in range(0, len(prac['tags'][i])):
        prac['tags'][i][j] = prac['tags'][i][j].lower()

prac_copy = copy.deepcopy(prac)
        
valid_array=[]
for i in range(0,len(prac)):
    valid_array.append(prac.iloc[i,:].tolist())


In [14]:
every_thing = copy.deepcopy(valid_array)

In [15]:
from collections import Counter

## 2. 예측 Modeling

In [16]:
import tqdm
def do_work(i):
    try:
        lst = every_thing[i]

        tag, song = [], []

        if len(lst[1]) == 0 and len(lst[2]) !=0 and len(lst[4])==0:
            tag, song = fn.fn_only_play(lst,model_tag,uniq_tag,len(every_thing),morphs,train_data)
        elif len(lst[1]) != 0 and len(lst[2]) !=0 and len(lst[4])==0:
            tag, song = fn.fn_tag_play(lst,model_tag,uniq_tag,len(every_thing),morphs,train_data)
        elif len(lst[1]) != 0 and len(lst[2]) ==0 and len(lst[4])==0:
            tag, song = fn.fn_only_tag(lst,model_tag,uniq_tag,len(every_thing),morphs,train_data)
        elif len(lst[1]) != 0 and len(lst[2]) ==0 and len(lst[4])!=0:
            tag, song = fn.fn_tag_song(lst,model_tag,uniq_tag,len(every_thing),morphs,train_data)
        elif len(lst[1]) == 0 and len(lst[2]) ==0 and len(lst[4])!=0:
            tag, song = fn.fn_only_song(lst,model_tag,for_genre,uniq_tag,genre_gn_all,len(every_thing),train_data)
            #print(i)

        if i%100== 0:
            print(i)

        if i%1000==0:
            time.sleep(5)

        return tag,song
    
    except Exception as ex:
        print(ex,'at ----> ',i,'\n')



if __name__ == '__main__':
    start_time = time.time()
    with Pool(processes=15) as p:
        result = p.map(do_work, range(0,len(every_thing)))
    print("--- %s seconds ---" % (time.time()-start_time))

/home/kys/.local/lib/python3.6/site-packages/gensim/models/word2vec.py:969: UserWarning: All the input context words are out-of-vocabulary for the current model.
  warnings.warn("All the input context words are out-of-vocabulary for the current model.")


0


/home/kys/.local/lib/python3.6/site-packages/gensim/models/word2vec.py:969: UserWarning: All the input context words are out-of-vocabulary for the current model.
  warnings.warn("All the input context words are out-of-vocabulary for the current model.")
/home/kys/.local/lib/python3.6/site-packages/gensim/models/word2vec.py:969: UserWarning: All the input context words are out-of-vocabulary for the current model.
  warnings.warn("All the input context words are out-of-vocabulary for the current model.")


5000


/home/kys/.local/lib/python3.6/site-packages/gensim/models/word2vec.py:969: UserWarning: All the input context words are out-of-vocabulary for the current model.
  warnings.warn("All the input context words are out-of-vocabulary for the current model.")
/home/kys/.local/lib/python3.6/site-packages/gensim/models/word2vec.py:969: UserWarning: All the input context words are out-of-vocabulary for the current model.
  warnings.warn("All the input context words are out-of-vocabulary for the current model.")
/home/kys/.local/lib/python3.6/site-packages/gensim/models/word2vec.py:969: UserWarning: All the input context words are out-of-vocabulary for the current model.
  warnings.warn("All the input context words are out-of-vocabulary for the current model.")


...

1600


/home/kys/.local/lib/python3.6/site-packages/gensim/models/word2vec.py:969: UserWarning: All the input context words are out-of-vocabulary for the current model.
  warnings.warn("All the input context words are out-of-vocabulary for the current model.")


3100
2400


/home/kys/.local/lib/python3.6/site-packages/gensim/models/word2vec.py:969: UserWarning: All the input context words are out-of-vocabulary for the current model.
  warnings.warn("All the input context words are out-of-vocabulary for the current model.")


5100
2000
4000
2800
900
4700
100
valid_data num is -->  481 and len is  82
4300
500
5500
1300
3200
3600
5200
1700
4800
2500
4400
4100
2900
200
2100
5600
1400
600
4900
1000
4500
3700
3300
5300
2600
1800
2200
5700
4200
3000
3400
list index out of range
'NoneType' object is not iterable at ---->  1074 

300
1500
5800
700
1100
7300
valid_data num is -->  333 and len is  100
4600
6200
3800
7700
2300
9600
7000
7400
10000
8100
5900
10400
6300
8500
1900
7800
7500
6600
8900
8200
10500
9700
6000
11200
9300
7900
10100
10800
8600
10600
7600
9000
7100
6700
8300
10200
11300
6100
9400
6400
8000
11400
list index out of range
'NoneType' object is not iterable at ---->  8353 

8700
9800
6800
10700
9100
7200
6500
9500
11600
10300
10900
8400
12300
9200
8800
11500
12700
14600
12400
13100
13500
12000
9900
11000
11700
15000
6900
13900
14300
12100
15800
14700
12500
13600
15400
13200
11100
16200
11800
12800
16900
14400
14000
15100
15900
14800
12600
12200
13300
13700
15500
16300
16600
11900
12900
14100
13800
17

In [17]:
def fn_only_play(lst,model_tag,uniq_tag,length,morphs,train_data):
    try:
        #for lst in data:
        # similarity 단어들
        words = []
        simi = model_tag.predict_output_word(lst[3],topn=30)

        # 유사도가 안나오니까 있는 명사만 넣자
        if simi == None:
            lst[6] = lst[3]

        # 유사도가 있는 경우
        else:

            for wr in simi:
                words.append(wr[0])


            # 유니크 태그(train)와 겹치는 similarity 단어들 / 겹치지 않는 단어들
            intr=[]
            nointr=[]
            for i in range(len(words)):
                if words[i] in uniq_tag:
                    intr.append(words[i])
                else:
                    nointr.append(words[i])

            # 최대 5개로 맞춤
            for i in range(len(intr)):
                if len(lst[6]) == 5:
                    break
                else:
                    if intr[i] not in lst[1]:
                        lst[6].append(intr[i])


            # 나머지는 similarity로 5개 맞추기
            if len(lst[6]) < 5:            
                for i in range(5-len(intr)):
                    if nointr[i] not in lst[1] and len(nointr[i]) >= 2:
                        lst[6].append(nointr[i])

            ###### 여기까지 5개씩 다 채움 #######
            # nouns 넣어주기(혹시 모르니까 길이가 긴 순서대로 넣어줌)

            lst[3].sort(key=len, reverse=True)

            if len(lst[6]) < 10:
                for i in range(len(lst[3])):
                    if len(lst[6]) == 10:
                        break
                    else:
                        if lst[3][i] in lst[6]:
                            pass
                        else:
                            if len(lst[3][i]) >= 2:
                                lst[6].append(lst[3][i])

            # words에서 안쓰인 것들 채우기 (한글자 제외)

            if len(lst[6]) < 10:
                for i in range(len(words)):
                    if len(lst[6]) == 10:
                        break
                    else:
                        if words[i] not in lst[6] and len(words[i])>=2:
                            lst[6].append(words[i])

            # 이래도 10개가 안찬다면 남은 것들 다 넣기
            if len(lst[6]) < 10:
                for i in range(len(words)):
                    if len(lst[6])==10:
                        break
                    else:
                        if words[i] not in lst[6]:
                            lst[6].append(words[i])

        update = lst[5]
        # 유사도 1순위
        b = model_tag.predict_output_word(lst[2],topn=10)

        # 유사도 1순위 없으면 song 빈 리스트로 남김
        if b==None:
            #print('No vocab')
            pass

        # 1순위 있을경우에는 pred_plylist 만들어줌
        else:
            final_len = len(lst[7])
            k = 1
            while final_len < 100:
                start = time.time()
                morph_len=len(lst[2])
                ind=0
                #print(k)
                a=[]
                while morph_len < (len(lst[2])+k):
                    if len(b[ind][0]) >1:
                        a.append(b[ind][0])
                        pred_plylist = list(set(sum([lst[2],a],[])))
                        morph_len = len(pred_plylist)
                        ind+=1
                        #print(pred_plylist)
                    else :
                        ind+=1

                #하나라도 만족하는 경우의 song들을 cand_songs에 append 하기
                cand_songs =[]
                for i in range(0,len(morphs)):
                    if (any(x in pred_plylist for x in morphs[i])):
                        #valid updt_date보다 이전의 playlist에서 찾아야함
                        if(train_data.updt_date[i] <= lst[5]):
                            show_sum = sum([x in pred_plylist for x in morphs[i]])
                            tmpp = [[x,show_sum] for x in train_data.songs[i]]
                            cand_songs.append(tmpp)

                # 모든 노래 후보
                cand_df = pd.DataFrame([y for x in cand_songs for y in x],columns=['song_num',"show_sum"]).sort_values(by='show_sum',ascending=False)
                sum_max = cand_df.groupby("song_num").max().sort_values("show_sum",ascending=False)
                sum_max

                # # 빈도수 상위 100개 뽑아서 song에 넣기
                c = Counter(cand_df.song_num)
                count_df_raw = pd.DataFrame(data=c.values(),index=c.keys(),columns=["count"])

                # 평균이 8이라서 count가 8 이상인 것만 뽑기
                count_df = count_df_raw[count_df_raw["count"] > 8]

                if len(count_df)>=100:
                    lst[7]=list(count_df.sort_values(by="count",ascending=False).iloc[0:100,:].index.values)
                else:
                    lst[7]=list(count_df_raw.sort_values(by="count",ascending=False).iloc[0:100,:].index.values)

                final_len = len(lst[7])
                k+=1

                all_song = []
                if k==9 and final_len != 100:
                    for i in range(0,len(train_data)):
                        if train_data.updt_date[i] <= lst[5]:
                            all_song.append(train_data.songs[i])
                        #print(all_song)
                    all_song_c = Counter(np.array(sum(all_song,[])))
                    all_song_sum = pd.DataFrame(data=all_song_c.values(),index = all_song_c.keys(),columns=['count']).sort_values(by="count",ascending=False)
                    first_len = 100-len(lst[7])
                    [lst[7].append(song) for song in all_song_sum.iloc[0:(100-len(lst[7])),:].index.tolist()]
                    all_song_len = len(set(lst[7]))
                    while all_song_len < 100 :
                        lst[7] = list(set(lst[7]))
                        second_len = first_len+(101-len(lst[7]))
                        [lst[7].append(song) for song in all_song_sum.iloc[(first_len+1):second_len,:].index.tolist()]
                        all_song_len = len(set(lst[7]))
                        first_len += second_len
                        print("valid_data num is --> ",lst[0],"and len is ",all_song_len)
                        
                        if len(all_song_sum)==all_song_len:
                            lst[7].extend(random.sample(list(range(0,50)),100-all_song_len))
                            all_song_len = len(lst[7])
                    final_len = len(lst[7])

                    break


        return lst[6], lst[7]
    
    except Exception as ex:
        print(ex)
        pass

lst = every_thing[481]
tag, song = fn.fn_only_play(lst,model_tag,uniq_tag,len(every_thing),morphs,train_data)

valid_data num is -->  481 and len is  82


In [101]:
lst

[481,
 [],
 ['끝', '이별'],
 ['이별', '끝'],
 [],
 '2005-01-20 00:23:40.000',
 ['슬픔', '아픔', '쓸쓸', '헤어짐', '이별노래', '이별', '헤어지', '이별후', '보고싶다', '겨울'],
 [241793,
  636034,
  533891,
  592260,
  337541,
  562050,
  689793,
  571529,
  86411,
  163468,
  641805,
  553486,
  400275,
  524181,
  691353,
  351131,
  477725,
  401310,
  251936,
  48677,
  26534,
  139815,
  279334,
  654757,
  323755,
  322348,
  126766,
  244348,
  505904,
  69810,
  220219,
  48316,
  563645,
  55614,
  18368,
  86977,
  204866,
  422595,
  651332,
  674884,
  238661,
  374850,
  619719,
  690761,
  478147,
  511941,
  319693,
  464974,
  325455,
  35280,
  390610,
  635991,
  289113,
  623836,
  179420,
  173149,
  100063,
  586208,
  370785,
  199522,
  534499,
  145122,
  559711,
  514912,
  626919,
  24423,
  243305,
  417386,
  70506,
  178796,
  447336,
  615275,
  653936,
  13937,
  38642,
  682996,
  676470,
  639607,
  34808,
  142969,
  320380,
  424703,
  5,
  33,
  40,
  36,
  30,
  29,
  7,
  39,
  3,
 

In [18]:
#1074 8353
pd.DataFrame(prac).head(10)

index                 tags                plylst_title             nouns  \
0      0                   []                          []                []   
1      1                   []                    [앨리스테이블]          [앨리스테이블]   
2      2                   []                          []                []   
3      3                   []                          []                []   
4      4                   []                          []                []   
5      5  [비, 분위기, 컨트리, 서정적인]                          []                []   
6      6                   []                          []                []   
7      7                   []                          []                []   
8      8               [스트레스]    [날, 스트레스, 빡시, 듬타, 운동, 리]  [스트레스, 날, 리, 운동]   
9      9                   []  [기분, 함께, 재즈, 좋, 만들, 하루, 달]   [기분, 달, 재즈, 하루]   

                                               songs                updt_date  \
0  [373313, 151080, 275346, 696876, 165237, 52593...  2019-05-27 14:14:33.000   
1                                                 []  2014-07-16 15:24:24.000   
2  [529437, 516103, 360067, 705713, 226062, 37089...  2008-06-21 23:26:22.000   
3  [589668, 21711, 570151, 320043, 13930, 599327,...  2017-10-30 18:15:43.000   
4  [672718, 121924, 102694, 683657, 201558, 38511...  2017-02-07 11:40:42.000   
5  [173033, 138237, 63140, 15733, 461780, 308519,...  2019-06-12 17:43:35.000   
6  [227044, 424672, 515592, 22408, 57893, 153714,...  2011-10-28 11:21:51.000   
7  [54457, 423722, 337682, 91214, 644980, 556444,...  2014-01-26 20:00:30.000   
8                                                 []  2017-02-09 17:33:45.000   
9                                                 []  2015-06-22 09:11:02.000   

  pred_tag pred_song  like_cnt  
0       []        []      1675  
1       []        []         1  
2       []        []        62  
3       []        []        20  
4       []        []        20  
5       []        []         2  
6       []        []         2  
7       []        []         3  
8       []        []       127  
9       []        []         0

In [22]:
prac.iloc[:,6] = pd.DataFrame(result).iloc[:,0]
prac.iloc[:,7] = pd.DataFrame(result).iloc[:,1]

In [23]:
for i in range(len(prac)):
    if prac.iloc[i,6] is None:
        prac.iloc[i,6] = [[0]]

In [41]:
for i in range(len(prac)):
    if prac.iloc[i,7] is None:
        prac.iloc[i,7] = [[0]]

In [24]:
for i in range(len(prac)):
    if prac.iloc[i,6] == [0]:
        del prac.iloc[i,6][-1]

In [42]:
for i in range(len(prac)):
    if prac.iloc[i,7] == [0]:
        del prac.iloc[i,7][-1]

In [25]:
for i in range(0,len(prac)):
    if len(prac.iloc[i,6])!=0:
        if len(prac.iloc[i,6])!=10:
            print(i,'yes')

1 yes
35 yes
221 yes
279 yes
384 yes
440 yes
498 yes
573 yes
613 yes
693 yes
807 yes
985 yes
1379 yes
1527 yes
1610 yes
1667 yes
1729 yes
1750 yes
1794 yes
1894 yes
2319 yes
2401 yes
2458 yes
2662 yes
2686 yes
2774 yes
2775 yes
2808 yes
2908 yes
3155 yes
3672 yes
3708 yes
3752 yes
3807 yes
3839 yes
3854 yes
3964 yes
3988 yes
4036 yes
4098 yes
4114 yes
4276 yes
4347 yes
4359 yes
4456 yes
4534 yes
4663 yes
4751 yes
4771 yes
4795 yes
4805 yes
5115 yes
5416 yes
5667 yes
5845 yes
5859 yes
5925 yes
5933 yes
5944 yes
6091 yes
6358 yes
6397 yes
6404 yes
6776 yes
6855 yes
6973 yes
6994 yes
7018 yes
7193 yes
7339 yes
7413 yes
7624 yes
7654 yes
7768 yes
7792 yes
7892 yes
7933 yes
7983 yes
8061 yes
8167 yes
8169 yes
8655 yes
8862 yes
8912 yes
8929 yes
8954 yes
9313 yes
9402 yes
9861 yes
9907 yes
10111 yes
10115 yes
10126 yes
10159 yes
10167 yes
10298 yes
10415 yes
10432 yes
10749 yes
11178 yes
11237 yes
11513 yes
11536 yes
11751 yes
11935 yes
12189 yes
12372 yes
12411 yes
12513 yes
12658 yes
12723

In [26]:
import numpy as np
plylst_tag_map = train_data[['id', 'tags']]

# unnest tags
plylst_tag_map_unnest = np.dstack(
    (
        np.repeat(plylst_tag_map.id.values, list(map(len, plylst_tag_map.tags))), 
        np.concatenate(plylst_tag_map.tags.values)
    )
)

# unnested 데이터프레임 생성 : plylst_tag_map
plylst_tag_map = pd.DataFrame(data = plylst_tag_map_unnest[0], columns = plylst_tag_map.columns)
plylst_tag_map['id'] = plylst_tag_map['id'].astype(str)

# unnest 객체 제거
del plylst_tag_map_unnest

In [27]:
plylst_tag_list_sort = plylst_tag_map.sort_values(by = ['id', 'tags']).groupby('id').tags.apply(list).reset_index(name = 'tag_list')

# 1. unnest 데이터프레임인 plylst_tag_map 테이블에서 태그 이름 정렬 후 list로 묶기
plylst_tag_list_sort = plylst_tag_map.sort_values(by = ['id', 'tags']).groupby('id').tags.apply(list).reset_index(name = 'tag_list')

# 2. 집계를 위해 1번 테이블에서 list 타입을 문자열 타입으로 변경
plylst_tag_list_sort['tag_list'] = plylst_tag_list_sort['tag_list'].astype(str)

# 3. 태그 리스트 별 매핑되는 플레이리스트 수 집계 테이블 생성 : tag_list_plylst_cnt
tag_list_plylst_cnt = plylst_tag_list_sort.groupby('tag_list').id.nunique().reset_index(name = 'plylst_cnt')

# 4. 매핑 수 기준 상위 10개 필터링
tag_list_plylst_cnt = tag_list_plylst_cnt.nlargest(10, 'plylst_cnt')

# 상위 top10 태그 리스트 만들기
top10_tags=[]
for i in range(len(np.array(tag_list_plylst_cnt['tag_list']))):
    top10_tags.append(re.compile('[가-힣]+').findall(np.array(tag_list_plylst_cnt['tag_list'])[i]))

import itertools
top10_tags = list(itertools.chain(*top10_tags))
top10_tags

['발라드',
 '팝',
 '락',
 '랩',
 '힙합',
 '댄스',
 '일렉',
 '뉴에이지',
 '소울',
 '알앤비',
 '기분전환',
 '휴식',
 '힐링',
 '밤',
 '새벽',
 '잔잔한']

In [28]:
# prac은 dataframe형태 => 채우는 것들이 모두 다 끝나고 마지막 점검 겸 
# nothing이었던 부분 채울 것임!!!! 그러니까 얘는 분리하는게 좋을듯!!! (분리해서 만들었어요~~)

for i in range(len(prac)):
    if len(prac.iloc[i,:][6]) < 10:
        for j in range(len(top10_tags)):
            if len(prac.iloc[i,:][6]) == 10:
                break
            else:
                if top10_tags[j] not in prac.iloc[i,:][1] + prac.iloc[i,:][6]:
                    prac.iloc[i,:][6].append(top10_tags[j])
prac.head(10)

index                 tags                plylst_title             nouns  \
0      0                   []                          []                []   
1      1                   []                    [앨리스테이블]          [앨리스테이블]   
2      2                   []                          []                []   
3      3                   []                          []                []   
4      4                   []                          []                []   
5      5  [비, 분위기, 컨트리, 서정적인]                          []                []   
6      6                   []                          []                []   
7      7                   []                          []                []   
8      8               [스트레스]    [날, 스트레스, 빡시, 듬타, 운동, 리]  [스트레스, 날, 리, 운동]   
9      9                   []  [기분, 함께, 재즈, 좋, 만들, 하루, 달]   [기분, 달, 재즈, 하루]   

                                               songs                updt_date  \
0  [373313, 151080, 275346, 696876, 165237, 52593...  2019-05-27 14:14:33.000   
1                                                 []  2014-07-16 15:24:24.000   
2  [529437, 516103, 360067, 705713, 226062, 37089...  2008-06-21 23:26:22.000   
3  [589668, 21711, 570151, 320043, 13930, 599327,...  2017-10-30 18:15:43.000   
4  [672718, 121924, 102694, 683657, 201558, 38511...  2017-02-07 11:40:42.000   
5  [173033, 138237, 63140, 15733, 461780, 308519,...  2019-06-12 17:43:35.000   
6  [227044, 424672, 515592, 22408, 57893, 153714,...  2011-10-28 11:21:51.000   
7  [54457, 423722, 337682, 91214, 644980, 556444,...  2014-01-26 20:00:30.000   
8                                                 []  2017-02-09 17:33:45.000   
9                                                 []  2015-06-22 09:11:02.000   

                                            pred_tag  \
0  [명곡, 록, 1990, 전설, 작품, 1980, 작곡가, 대표, world, rock]   
1       [앨리스테이블, 발라드, 팝, 락, 랩, 힙합, 댄스, 일렉, 뉴에이지, 소울]   
2  [모음, 솔로, 오디오, 플레이리스트, 태연, bgm, 2020, 상시, 2010년...   
3  [포크, 밴드, 뮤지션, 싱어송라이터, 인디, 얼터너티브, 아날로그, 2000, 한...   
4      [ccm, 워십, 찬양, 은혜, 국내ccm, 인기, 추천, 좋아하, 교회, 아이]   
5  [jazz, 포크, 블루스, 거리, 어쿠스틱, 포크/블루스/컨트리, 인디, 올드팝,...   
6  [일렉트로닉, 하우스, 신스팝, party, club, 트랜스, 테크하우스, mus...   
7  [일렉, dance, 하우스, house, 디스코, 테크노, 파티, 트랜스, 일렉트...   
8        [기분, 신나, 흔들, up, 전환, 운동, 달리, 여름, 성인가요, 트렌디]   
9         [시작, 오늘, 연인, 하루, jazz, 기분, 재즈, 커피, 함께, 위로]   

                                           pred_song  like_cnt  
0                                                 []      1675  
1                                                 []         1  
2                                                 []        62  
3                                                 []        20  
4                                                 []        20  
5                                                 []         2  
6                                                 []         2  
7                                                 []         3  
8  [459256, 355939, 254865, 130199, 445170, 42039...       127  
9  [663256, 177460, 705515, 366786, 140867, 32172...         0

In [29]:
import ast
song_final = pd.read_csv("song_final_df(2).csv", names=prac.columns.tolist(),header=0, converters = {"pred_song":ast.literal_eval})
tag_final = pd.read_csv("tag_song_final_df.csv",names=prac.columns.tolist(),header=0, converters = {"pred_song":ast.literal_eval})

In [30]:
idx = np.where(np.array(prac['index'].isin(song_final['index']))==False)

In [31]:
tmpp = pd.DataFrame(np.zeros(len(idx[0])*9).reshape(len(idx[0]),9).astype(int),columns=song_final.columns.tolist())
tmpp['index'] = idx[0]
song_final = pd.concat([song_final,tmpp],ignore_index=True).sort_values(by=['index']).reset_index(drop=True)

In [32]:
for i in range(len(prac)):
    if song_final.pred_song[i]!=0 :
        prac.iloc[i,7].extend(song_final.iloc[i,7])

In [33]:
idx2 = np.where(np.array(prac['index'].isin(tag_final['index']))==False)

tmpp2 = pd.DataFrame(np.zeros(len(idx2[0])*9).reshape(len(idx2[0]),9),columns=tag_final.columns.tolist())
tmpp2['index'] = idx2[0]
tag_final = pd.concat([tag_final,tmpp2],ignore_index=True).sort_values(by=['index']).reset_index(drop=True)

In [34]:
for i in range(len(prac)):
    if tag_final.pred_song[i]!=0 :
        prac.iloc[i,7].extend(tag_final.iloc[i,7])

# Fill the None

In [35]:
tmp = [y for x in train_data["songs"] for y in x]

# 트레인에 노래들 빈도 수 계산

In [36]:
from collections import Counter
pp = pd.DataFrame(data=Counter(tmp).values(),index=Counter(tmp).keys(),columns=["count"]).sort_values(by=['count'],ascending=False)

# 상위 1000개 빈도수를 갖는 노래들 저장

In [37]:
tmp_list = []
for i in pp.index[0:1000]:
    tmp_list.append(song_meta["song_name"][song_meta["id"]==i])
tmp_list    

[144663    밤편지
 Name: song_name, dtype: object,
 116573    안아줘
 Name: song_name, dtype: object,
 357367    비
 Name: song_name, dtype: object,
 366786    가끔 미치도록 네가 안고 싶어질 때가 있어
 Name: song_name, dtype: object,
 654757    눈의 꽃
 Name: song_name, dtype: object,
 133143    그대와 나, 설레임 (Feat. 소울맨)
 Name: song_name, dtype: object,
 349492    어떤이별
 Name: song_name, dtype: object,
 675115    야생화
 Name: song_name, dtype: object,
 463173    비가 내렸어 (Vocal by 스티브언니)
 Name: song_name, dtype: object,
 42155    벙어리
 Name: song_name, dtype: object,
 610933    널 생각해
 Name: song_name, dtype: object,
 396828    쉬운사랑
 Name: song_name, dtype: object,
 461341    어떻게 지내
 Name: song_name, dtype: object,
 174749    비도 오고 그래서 (Feat. 신용재)
 Name: song_name, dtype: object,
 520093    고마운 사람 (Vocal by 이소진)
 Name: song_name, dtype: object,
 701557    우연히 봄
 Name: song_name, dtype: object,
 549178    금요일에 만나요 (Feat. 장이정 Of HISTORY)
 Name: song_name, dtype: object,
 485155    선물
 Name: song_name, dtype: object,
 650494

# for wrong date (ex. 20170000) no month no date

In [38]:
song_meta["issue_date"] = song_meta["issue_date"].astype(str)

In [39]:
for i in range(len(tmp_list)):
    song_meta["issue_date"][tmp_list[i].index[0]] =  song_meta["issue_date"][tmp_list[i].index[0]][:4] + \
                                                re.sub('00','01',song_meta["issue_date"][tmp_list[i].index[0]][4:6]) + \
                                                song_meta["issue_date"][tmp_list[i].index[0]][6:]
     
    song_meta["issue_date"][tmp_list[i].index[0]] = song_meta["issue_date"][tmp_list[i].index[0]][:6] + \
                                                re.sub('00','01',song_meta["issue_date"][tmp_list[i].index[0]][6:]) 
        
    print(i)

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.
/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  import sys


0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

### 노리스트에 채울 노래들을 저장하는데 1000개 노래들을 1부터 순서대로 채운다.
### 단, 앨범 업데이트 날짜 이전에 출시된 노래들만 비교해서 넣기

In [43]:
from dateutil.parser import parse
for i in range(len(prac)):
    if len(prac.iloc[i,7])==0:
        for j in range(len(tmp_list)):
            if len(prac.iloc[i,7]) == 100:
                break
            if parse(prac.iloc[i,5]) > parse(song_meta["issue_date"][tmp_list[j].index[0]]):
                prac.iloc[i,7].append(tmp_list[j].index[0])


In [119]:
#prac.iloc[481,7] = pd.Series(lst[7])

for i in range(len(prac.iloc[481,7])):
    prac.iloc[481,7][i] = lst[7][i]

In [45]:
for i in range(0,len(prac)):
    if len(prac.pred_tag[i])!=10 :
        print(i,'yes')

In [44]:
for i in range(0,len(prac)):
    if len((set(prac.pred_song[i])))%100!=0 :
        print(i,'yes')

In [50]:
for i in range(0,len(prac)):
    print(len(prac.pred_song[i]))

100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100


100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100


100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100


100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100


100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100


100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100


100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100
100


In [49]:
for i in range(len(prac)):
    prac.pred_song[i] = list(set(prac.pred_song[i]))

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


### 2-1. 예측 된 것 확인

In [138]:
prac

index                         tags plylst_title     nouns  \
0          0                           []           []        []   
1          1                           []     [앨리스테이블]  [앨리스테이블]   
2          2                           []           []        []   
3          3                           []           []        []   
4          4                           []           []        []   
...      ...                          ...          ...       ...   
23010  23010                        [잔잔한]           []        []   
23011  23011  [어머니, 힘들때, 아빠, 가족, 위로받고싶을때]           []        []   
23012  23012                           []           []        []   
23013  23013                           []           []        []   
23014  23014                           []           []        []   

                                                   songs  \
0      [373313, 151080, 275346, 696876, 165237, 52593...   
1                                                     []   
2      [529437, 516103, 360067, 705713, 226062, 37089...   
3      [589668, 21711, 570151, 320043, 13930, 599327,...   
4      [672718, 121924, 102694, 683657, 201558, 38511...   
...                                                  ...   
23010  [75842, 26083, 244183, 684715, 500593, 508608,...   
23011  [450275, 487671, 561031, 663944, 628672, 59121...   
23012  [625875, 464051, 11657, 236393, 358186, 213435...   
23013  [161094, 665833, 688145, 432735, 439938, 12665...   
23014  [643070, 132994, 98223, 293236, 513129, 650494...   

                     updt_date  \
0      2019-05-27 14:14:33.000   
1      2014-07-16 15:24:24.000   
2      2008-06-21 23:26:22.000   
3      2017-10-30 18:15:43.000   
4      2017-02-07 11:40:42.000   
...                        ...   
23010  2015-12-17 14:06:05.000   
23011  2020-04-16 21:35:44.000   
23012  2019-03-27 15:27:40.000   
23013  2015-11-18 11:49:09.000   
23014  2017-04-23 16:50:58.000   

                                                pred_tag  \
0      [명곡, 록, 1990, 전설, 작품, 1980, 작곡가, 대표, world, rock]   
1           [앨리스테이블, 발라드, 팝, 락, 랩, 힙합, 댄스, 일렉, 뉴에이지, 소울]   
2      [모음, 솔로, 오디오, 플레이리스트, 태연, bgm, 2020, 상시, 2010년...   
3      [포크, 밴드, 뮤지션, 싱어송라이터, 인디, 얼터너티브, 아날로그, 2000, 한...   
4          [ccm, 워십, 찬양, 은혜, 국내ccm, 인기, 추천, 좋아하, 교회, 아이]   
...                                                  ...   
23010         [공부, 커피, 피아노, 위로, 낮잠, 새벽, 회상, 퇴근길, 겨울, 많이]   
23011        [엄마, 위로, 응원, 부모님, 성인가요, 힘내, 상처, 청춘, 부모, 아이]   
23012  [록, 명곡, 내한, 작곡가, 레이블, 1990, 전설, 해외알앤비소울, 프로듀싱,...   
23013  [오케스트라, 클래식, 연주, 유치원, virtuoso, 협주곡, classic, ...   
23014           [가요, 뮤지컬, 랩, 락, 가을, 위하, 알앤비, 명곡, 가수, 남자]   

                                               pred_song  like_cnt  
0      [72705, 271361, 187395, 299019, 260107, 15376,...      1675  
1      [116573, 366786, 654757, 133143, 675115, 61093...         1  
2      [56324, 628232, 107530, 672271, 435732, 261659...        62  
3      [642056, 527883, 659979, 536588, 655889, 51150...        20  
4      [223752, 435729, 244245, 614938, 44570, 145438...        20  
...                                                  ...       ...  
23010  [235522, 579592, 330761, 432653, 440848, 47669...        17  
23011  [667138, 104450, 677893, 593925, 523, 666130, ...        10  
23012  [380423, 593932, 11797, 646677, 140310, 112153...         0  
23013  [495620, 679436, 511508, 558622, 415774, 51203...        31  
23014  [544258, 444936, 177673, 592405, 192536, 43932...        19  

[23015 rows x 9 columns]

In [51]:
valid_final = pd.DataFrame([valid_data.id,prac.pred_song,prac.pred_tag])
valid_final = valid_final.rename(index={'id':'id','pred_song':'songs','pred_tag':'tags'})
#valid_final.columns = ['']*len(valid_final.columns)
#valid_final.columns = [["id",'songs','tags']]
valid_final.head()

0      \
id                                                118598   
songs  [72705, 271361, 187395, 299019, 260107, 15376,...   
tags   [명곡, 록, 1990, 전설, 작품, 1980, 작곡가, 대표, world, rock]   

                                                   1      \
id                                                131447   
songs  [109574, 579592, 521739, 549392, 440848, 13314...   
tags        [앨리스테이블, 발라드, 팝, 락, 랩, 힙합, 댄스, 일렉, 뉴에이지, 소울]   

                                                   2      \
id                                                 51464   
songs  [56324, 628232, 107530, 672271, 435732, 261659...   
tags   [모음, 솔로, 오디오, 플레이리스트, 태연, bgm, 2020, 상시, 2010년...   

                                                   3      \
id                                                 45144   
songs  [642056, 527883, 536588, 659979, 655889, 51150...   
tags   [포크, 밴드, 뮤지션, 싱어송라이터, 인디, 얼터너티브, 아날로그, 2000, 한...   

                                                   4      \
id                                                 79929   
songs  [223752, 435729, 244245, 44570, 614938, 145438...   
tags       [ccm, 워십, 찬양, 은혜, 국내ccm, 인기, 추천, 좋아하, 교회, 아이]   

                                                   5      \
id                                                138538   
songs  [30221, 194589, 391717, 192042, 231469, 352303...   
tags   [jazz, 포크, 블루스, 거리, 어쿠스틱, 포크/블루스/컨트리, 인디, 올드팝,...   

                                                   6      \
id                                                127575   
songs  [18954, 194572, 163344, 177168, 251410, 511509...   
tags   [일렉트로닉, 하우스, 신스팝, party, club, 트랜스, 테크하우스, mus...   

                                                   7      \
id                                                115317   
songs  [296448, 455683, 245255, 611849, 1546, 355345,...   
tags   [일렉, dance, 하우스, house, 디스코, 테크노, 파티, 트랜스, 일렉트...   

                                                   8      \
id                                                 80810   
songs  [443914, 536588, 65053, 548896, 473639, 277034...   
tags         [기분, 신나, 흔들, up, 전환, 운동, 달리, 여름, 성인가요, 트렌디]   

                                                   9      ...  \
id                                                142007  ...   
songs  [476680, 320530, 133143, 154648, 482340, 33829...  ...   
tags          [시작, 오늘, 연인, 하루, jazz, 기분, 재즈, 커피, 함께, 위로]  ...   

                                                   23005  \
id                                                136258   
songs  [626700, 409613, 278551, 622615, 142360, 59446...   
tags        [휴양지, 바다, 시원한, 여름, 여행, 해변, 더위, 뜨겁, 시원, 고속도로]   

                                                   23006  \
id                                                 92067   
songs  [377355, 232978, 215067, 598047, 292896, 27037...   
tags   [록, 명곡, 1990, 대표, rock, 메탈, 전설, 1980, world, p...   

                                                   23007  \
id                                                 44013   
songs  [1546, 95754, 269356, 577075, 545334, 605244, ...   
tags    [감미로운, 어쿠스틱, 여유, 봄, 산책, 추억회상, 감미, 카페음악, 잔잔한, 가요]   

                                                   23008  \
id                                                100684   
songs  [422915, 586760, 341513, 383498, 133143, 39682...   
tags           [설렘, 곡, 요즘, 겨울, 띵곡, 음악마중, 부록, 별책, 남자, 부르]   

                                                   23009  \
id                                                 17766   
songs  [704005, 607251, 468500, 220693, 285721, 11113...   
tags   [듣도보도못한굿뮤직, 소울, 네오소울, rnb, rnbsoul, 앤비, 어반, so...   

                                                   23010  \
id                                                101722   
songs  [235522, 579592, 330761, 432653, 440848, 47669...   
tags          [공부, 커피, 피아노, 위로, 낮잠, 새벽, 회상, 퇴근길, 겨울, 많이]   

                                                   23011  \
id                                                122127   
songs  [667138, 104450, 677893, 593925, 523, 666130, ..

In [52]:
valid_list = []
for i in range(0,len(valid_final.columns)):
    valid_list.append(valid_final.iloc[:,i].to_dict())
valid_list

[{'id': 118598,
  'songs': [72705,
   271361,
   187395,
   299019,
   260107,
   15376,
   392210,
   318487,
   161821,
   177701,
   276521,
   336940,
   102445,
   243248,
   126000,
   21558,
   326204,
   195650,
   438851,
   357967,
   396369,
   373850,
   207973,
   216696,
   395904,
   486028,
   151183,
   415376,
   464019,
   390294,
   594592,
   196261,
   175783,
   178860,
   281774,
   87223,
   436410,
   267452,
   188610,
   357064,
   77517,
   10445,
   425680,
   166099,
   576729,
   391389,
   570599,
   695032,
   249594,
   115468,
   373006,
   112399,
   387859,
   328994,
   39725,
   488753,
   510258,
   493381,
   264014,
   325455,
   576848,
   602448,
   666451,
   365398,
   157022,
   414561,
   201075,
   371072,
   13198,
   55696,
   279963,
   256930,
   497577,
   152489,
   640428,
   591789,
   150446,
   208812,
   117169,
   230837,
   325047,
   83907,
   59849,
   607179,
   616907,
   225228,
   178124,
   540122,
   260576,
   6517

In [53]:
import json
# with open("result.json", 'w',encoding='utf-8') as outfile:
#     json.dump(valid_list, outfile, indent=4)

import os
import distutils.dir_util
import io

def write_json(data, fname):
    def _conv(o):
        if isinstance(o, (np.int64, np.int32)):
            return int(o)
        raise TypeError

    parent = os.path.dirname(fname)
    distutils.dir_util.mkpath("./arena_data/" + parent)
    with io.open("./arena_data/" + fname, "w", encoding="utf-8") as f:
        json_str = json.dumps(data, ensure_ascii=False, default=_conv)
        f.write(json_str)
        
write_json(valid_list, 'result.json')

In [54]:
def load_json(fname):
    with open(fname, encoding="utf-8") as f:
        json_obj = json.load(f)

    return json_obj

load_json("./arena_data/result.json")

[{'id': 118598,
  'songs': [72705,
   271361,
   187395,
   299019,
   260107,
   15376,
   392210,
   318487,
   161821,
   177701,
   276521,
   336940,
   102445,
   243248,
   126000,
   21558,
   326204,
   195650,
   438851,
   357967,
   396369,
   373850,
   207973,
   216696,
   395904,
   486028,
   151183,
   415376,
   464019,
   390294,
   594592,
   196261,
   175783,
   178860,
   281774,
   87223,
   436410,
   267452,
   188610,
   357064,
   77517,
   10445,
   425680,
   166099,
   576729,
   391389,
   570599,
   695032,
   249594,
   115468,
   373006,
   112399,
   387859,
   328994,
   39725,
   488753,
   510258,
   493381,
   264014,
   325455,
   576848,
   602448,
   666451,
   365398,
   157022,
   414561,
   201075,
   371072,
   13198,
   55696,
   279963,
   256930,
   497577,
   152489,
   640428,
   591789,
   150446,
   208812,
   117169,
   230837,
   325047,
   83907,
   59849,
   607179,
   616907,
   225228,
   178124,
   540122,
   260576,
   6517